In [1]:
#!pip install tdqm geopy
#!pip install folium

In [2]:
import pandas as pd
import numpy as np
import boto3
from tqdm.notebook import trange, tqdm
from math import cos, radians, nan
import geopy.distance
import folium
import folium.plugins
import branca
import branca.colormap as cm

from add_labels import km_to_lat_lon_displacement

In [3]:
# def km_to_lat_lon_displacement(km, origin_latitude):
#     lat = km/111.111
#     lon = km/(111.111 * cos(radians(origin_latitude)))
#     return lat, lon


def calculate_weighted_index(center, survey_data, radius):
    
    try:
        lon, lat = tuple(map(float, center.strip("()").split(', ')))
    except:
        print("ERROR: unable to extract latitude and logitude data from the center column")
    
    weighted_index = nan
    point_count = 0
    index_range = nan
    
    latOffset, lonOffset = km_to_lat_lon_displacement(radius + 1, lat)
    
    first_subset = survey_data[
        ((lat - latOffset)  < survey_data['lat']) & (survey_data['lat'] < (lat + latOffset)) &
        ((lon - lonOffset)  < survey_data['lon']) & (survey_data['lon'] < (lon + lonOffset))
    ]
    
    if len(first_subset) > 0:
        first_subset["distance"] = first_subset.apply(lambda inner_row: geopy.distance.distance((lat, lon), (inner_row["lat"], inner_row["lon"])).km, axis=1)
        second_subset = first_subset[first_subset["distance"] < radius]
        
    #    
    #    if len(inside_radius) > 0:
    #        ##### Weighted average calculations are done here
    #        min_wealth_index = np.min(inside_radius.wealth_index)
    #        max_wealth_index = np.max(inside_radius.wealth_index)
    #        min_distance = np.min(inside_radius.distance)
    #        max_distance = np.max(inside_radius.distance)
    #        index_range =  max_wealth_index - min_wealth_index
    #        point_count = len(inside_radius)

    #        if min_distance == 0.0: #case where its close or the same coordinate (zero)
    #            inside_radius.loc[inside_radius["distance"] < 0.01,'distance'] = 0.01
    
      #      inverse_weight = radius / inside_radius.distance
      #      inside_radius["weight"] = inverse_weight

            #This is the weighted calculation
     #       weighted_index = np.sum((inside_radius.wealth_index * inside_radius.weight)) / np.sum(inside_radius.weight)

            # to remove confusion, weighted_index is set to NaN when there are no points
      #      if point_count == 0:
      #          weighted_index = nan

            ##########
            
    return first_subset, second_subset
        
        
    #return weighted_index, point_count, index_range

In [4]:
# Load image meta data with density indicator
meta_data = pd.read_csv("s3://w210-poverty-mapper/modeling/metadata/total_meta_data_full_updated_density.csv")
# Load dhs wealth index data
dhs_data = pd.read_csv("s3://w210-poverty-mapper/modeling/metadata/dhs_wealth_index_boundaries.csv")
# Load wealth index calculations
calculations = pd.read_csv("s3://w210-poverty-mapper/modeling/metadata/meta_data_labels_density.csv")

In [5]:
# Subset meta data to keep populated areas and full images
meta_data_subset = meta_data[
    (meta_data["Density"] == 1) & 
    (meta_data["partial_updated"] == False)
]

In [6]:
# Subset dhs wealth index data to keep valid points
dhs_data_subset = dhs_data[dhs_data["inside_boundaries"] == True]

In [7]:
# Set radius list 
radius = 10

In [8]:
first_subset, second_subset = calculate_weighted_index(meta_data_subset["center"][109542], dhs_data, radius)

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [23]:
first_subset.shape
#second_subset.shape

(13, 8)

In [10]:
calculations.iloc[109542]

filename           sentinel2_composite/transformed_data/51P/530-0...
zone                                                             51P
center                      (120.90073885511106, 14.406304629864561)
lat_lon_bounds     [(120.89054868366185, 14.416579016400146), (12...
utm_bounds         BoundingBox(left=919660.0, bottom=1595110.0, r...
countries                                            ['Philippines']
partial_updated                                                False
weighted_index                                               85.1447
point_count                                                        7
index_range                                                  19.0201
Density                                                            1
Name: 109542, dtype: object

In [12]:
point = meta_data_subset["center"][109542].strip("()").split(', ')
print(point )

['120.90073885511106', '14.406304629864561']


In [13]:
# Plot full data

# Create base map
colormap = cm.LinearColormap(colors=["red", "orange", "yellow", "lightgreen", "green"], index=[0, 25, 50, 75, 100],vmin=0,vmax=100)

map = folium.Map(location=[38, 69], 
                 zoom_start=8, 
                 control_scale=True)

# Add cluster GPS coordinates with pop-up
for index, location_info in dhs_data_subset.iterrows():
    folium.Circle([location_info["lat"],
                   location_info["lon"]], 
                  radius=2,
                  color=colormap(location_info["wealth_index"]),
                  popup=location_info[["country", "cluster", "wealth_index"]]).add_to(map)
    
   # folium.Marker(location=[point[1], point[0]]).add_to(map)


map.add_child(colormap)

In [14]:
# Plot first subset

# Create base map
colormap = cm.LinearColormap(colors=["red", "orange", "yellow", "lightgreen", "green"], index=[0, 25, 50, 75, 100],vmin=0,vmax=100)

map = folium.Map(location=[38, 69], 
                 zoom_start=8, 
                 control_scale=True)

# Add cluster GPS coordinates with pop-up
for index, location_info in first_subset.iterrows():
    folium.Circle([location_info["lat"],
                   location_info["lon"]], 
                  radius=2,
                  color=colormap(location_info["wealth_index"]),
                  popup=location_info[["country", "cluster", "wealth_index"]]).add_to(map)
    
    folium.Marker(location=[point[1], point[0]]).add_to(map)

map.add_child(colormap)

In [15]:
# Plot first subset

# Create base map
colormap = cm.LinearColormap(colors=["red", "orange", "yellow", "lightgreen", "green"], index=[0, 25, 50, 75, 100],vmin=0,vmax=100)

map = folium.Map(location=[38, 69], 
                 zoom_start=8, 
                 control_scale=True)

# Add cluster GPS coordinates with pop-up
for index, location_info in second_subset.iterrows():
    folium.Circle([location_info["lat"],
                   location_info["lon"]], 
                  radius=2,
                  color=colormap(location_info["wealth_index"]),
                  popup=location_info[["country", "cluster", "wealth_index"]]).add_to(map)
    
    folium.Marker(location=[point[1], point[0]]).add_to(map)

map.add_child(colormap)